In [0]:
jdbcHostname = "server4traffic.database.windows.net"
jdbcDatabase = "datawarehouse04"
jdbcPort = 1433
jdbcUsername = "admin2traffic"
jdbcPassword = "abcd1234@"

In [0]:
# URL JDBC
jdbcUrl = f"jdbc:sqlserver://{jdbcHostname}:{jdbcPort};database={jdbcDatabase};encrypt=true;trustServerCertificate=false;hostNameInCertificate=*.database.windows.net;loginTimeout=30;"

# Paramètres de connexion
connectionProperties = {
  "user" : jdbcUsername,
  "password" : jdbcPassword,
  "driver" : "com.microsoft.sqlserver.jdbc.SQLServerDriver"
}

In [0]:
dbutils.widgets.text("date_param", "")
date_a_traiter = dbutils.widgets.get("date_param")

In [0]:
# construire la requête SQL avec filtre
query = f"(SELECT * FROM raw.visiteurs WHERE CAST(timestamp_insertion AS DATE) = '{date_a_traiter}') AS visiteurs_filtrés"

# lire uniquement les données de la veille
df_visiteurs = spark.read.jdbc(
    url=jdbcUrl,
    table=query,
    properties=connectionProperties
)

In [0]:
import pyspark.sql.functions as F

In [0]:
# Lire Toute la table SQL dans un DataFrame Spark
# df_visiteurs = spark.read.jdbc(url=jdbcUrl, table="raw.visiteurs", properties=connectionProperties)

In [0]:
display(df_visiteurs.limit(10))

store_id sensor_id date heure nb_visiteurs timestamp_insertion

In [0]:
# Compter les lignes où AU MOINS UNE colonne est null
nb_lignes_null = df_visiteurs.filter(
    F.col("store_id").isNull() |
    F.col("sensor_id").isNull() |
    F.col("nb_visiteurs").isNull() |
    F.col("date").isNull() |
    F.col("heure").isNull()
).count()

In [0]:
print(f"Nombre de lignes avec au moins un null : {nb_lignes_null}")

Nombre de lignes avec au moins un null : 30585


In [0]:
df_visiteurs = df_visiteurs.dropna()


In [0]:
# Compter les lignes où AU MOINS UNE colonne est null
nb_lignes_null = df_visiteurs.filter(
    F.col("store_id").isNull() |
    F.col("sensor_id").isNull() |
    F.col("nb_visiteurs").isNull() |
    F.col("date").isNull() |
    F.col("heure").isNull()
).count()
print(f"Nombre de lignes avec au moins un null : {nb_lignes_null}")

Nombre de lignes avec au moins un null : 0


In [0]:
df_visiteurs = df_visiteurs.withColumn("nb_visiteurs", F.col("nb_visiteurs").cast("int"))

In [0]:
df_visiteurs.select("nb_visiteurs").describe().show()

+-------+------------------+
|summary|      nb_visiteurs|
+-------+------------------+
|  count|            880755|
|   mean|15.925747795925087|
| stddev| 86.97177940862738|
|    min|              -999|
|    max|              1189|
+-------+------------------+



# **SQL**

In [0]:
# Enregistrer le DataFrame comme une table temporaire
df_visiteurs.createOrReplaceTempView("visiteurs")

**Nettoyer la colonne Date**


In [0]:
spark.sql("""
    select distinct date
    from visiteurs
    where date like "%/%/%"
""").show()

+----------+
|      date|
+----------+
|10/05/2023|
|30/04/2023|
|2023/04/30|
|2023/05/03|
|2023/05/02|
|2023/05/06|
|29/04/2023|
|28/04/2023|
|2023/05/07|
|07/05/2023|
|2023/04/28|
|2023/05/05|
|04/05/2023|
|03/05/2023|
|2023/05/01|
|2023/05/10|
|2023/05/09|
|2023/04/29|
|09/05/2023|
|08/05/2023|
+----------+
only showing top 20 rows



In [0]:
spark.sql("""
    select distinct date
    from visiteurs
    where date like "%-%/%"
""").show()

+----+
|date|
+----+
+----+



In [0]:
spark.sql("""
    select distinct date
    from visiteurs
    where date like "%-%-2024"
""").show()

+----+
|date|
+----+
+----+



In [0]:
clean_visiteurs = spark.sql("""
    SELECT 
        store_id, 
        sensor_id, 
        COALESCE(
            TO_DATE(date, 'yyyy-MM-dd'), 
            TO_DATE(date, 'yyyy/MM/dd'),
            TO_DATE(date, 'dd/MM/yyyy')
        ) AS date, 
        hour(CAST(heure AS TIMESTAMP)) AS heure, 
        nb_visiteurs
    FROM visiteurs
""")
clean_visiteurs.createOrReplaceTempView("clean_visiteurs")
display(clean_visiteurs)

store_id sensor_id date heure nb_visiteurs 1 1 2023-04-27 9 25 1 1 2023-04-27 10 55 1 1 2023-04-27 11 62 1 1 2023-04-27 12 64 1 1 2023-04-27 13 89 1 1 2023-04-27 14 52 1 1 2023-04-27 15 50 1 1 2023-04-27 16 48 1 1 2023-04-27 17 77 1 1 2023-04-27 18 89 1 1 2023-04-27 19 0 1 1 2023-04-27 20 0 1 1 2023-04-27 21 0 1 1 2023-04-27 22 0 1 1 2023-04-27 23 0 1 2 2023-04-27 9 17 1 2 2023-04-27 11 35 1 2 2023-04-27 12 373 1 2 2023-04-27 13 53 1 2 2023-04-27 14 33 1 2 2023-04-27 15 41 1 2 2023-04-27 16 41 1 2 2023-04-27 17 64 1 2 2023-04-27 18 64 1 2 2023-04-27 19 0 1 2 2023-04-27 20 0 1 2 2023-04-27 21 0 1 2 2023-04-27 22 0 1 2 2023-04-27 23 0 1 3 2023-04-27 9 27 1 3 2023-04-27 10 47 1 3 2023-04-27 11 51 1 3 2023-04-27 12 59 1 3 2023-04-27 13 76 1 3 2023-04-27 14 47 1 3 2023-04-27 15 54 1 3 2023-04-27 16 51 1 3 2023-04-27 17 74 1 3 2023-04-27 18 79 1 3 2023-04-27 19 0 1 3 2023-04-27 20 0 1 3 2023-04-27 21 0 1 3 2023-04-27 22 0 1 3 2023-04-27 23 0 1 4 2023-04-27 9 19 1 4 2023-04-27 10 30 1 4 2023-04-27 11 34 1 4 2023-04-27 12 41 1 4 2023-04-27 13 57 1 4 2023-04-27 14 42 1 4 2023-04-27 15 43 1 4 2023-04-27 16 41 1 4 2023-04-27 17 51 1 4 2023-04-27 18 65 1 4 2023-04-27 19 0 1 4 2023-04-27 20 -999 1 4 2023-04-27 21 0 1 4 2023-04-27 22 0 1 4 2023-04-27 23 0 1 5 2023-04-27 9 25 1 5 2023-04-27 0 38 1 5 2023-04-27 11 54 1 5 2023-04-27 13 75 1 5 2023-04-27 14 51 1 5 2023-04-27 15 48 1 5 2023-04-27 16 51 1 5 2023-04-27 18 74 1 5 2023-04-27 19 0 1 5 2023-04-27 20 0 1 5 2023-04-27 21 0 1 5 2023-04-27 22 0 1 5 2023-04-27 23 0 1 6 2023-04-27 9 20 1 6 2023-04-27 10 34 1 6 2023-04-27 11 38 1 6 2023-04-27 12 40 1 6 2023-04-27 13 60 1 6 2023-04-27 14 41 1 6 2023-04-27 0 36 1 6 2023-04-27 16 36 1 6 2023-04-27 17 55 1 6 2023-04-27 18 49 1 6 2023-04-27 19 0 1 6 2023-04-27 20 0 1 6 2023-04-27 21 0 1 6 2023-04-27 22 0 1 6 2023-04-27 23 0 1 7 2023-04-27 9 14 1 7 2023-04-27 10 21 1 7 2023-04-27 11 30 1 7 2023-04-27 12 32 1 7 2023-04-27 13 48 1 7 2023-04-27 14 31 1 999 2023-04-27 16 26 1 7 2023-04-27 17 48 1 7 2023-04-27 18 47 1 7 2023-04-27 19 0 1 7 2023-04-27 20 0 1 7 2023-04-27 21 0 1 7 2023-04-27 22 0 1 7 2023-04-27 23 0 1 8 2023-04-27 9 17 1 8 2023-04-27 10 23 1 8 2023-04-27 11 25 1 8 2023-04-27 12 0 1 8 2023-04-27 13 49 1 8 2023-04-27 14 30 1 8 2023-04-27 15 29 1 8 2023-04-27 16 26 1 8 2023-04-27 17 39 1 8 2023-04-27 18 45 1 8 2023-04-27 19 0 1 8 2023-04-27 20 0 1 8 2023-04-27 21 0 1 8 2023-04-27 22 0 1 8 2023-04-27 23 0 1 9 2023-04-27 9 30 1 9 2023-04-27 10 41 1 9 2023-04-27 11 53 1 9 2023-04-27 12 68 1 9 2023-04-27 13 77 1 9 2023-04-27 14 50 1 9 2023-04-27 15 53 1 9 2023-04-27 16 55 1 9 2023-04-27 17 87 1 9 2023-04-27 18 80 1 9 2023-04-27 19 0 1 9 2023-04-27 20 0 1 9 2023-04-27 21 0 1 9 2023-04-27 22 0 1 9 2023-04-27 23 0 1 10 2023-04-27 9 16 1 10 2023-04-27 10 27 1 10 2023-04-27 12 43 1 10 2023-04-27 13 50 1 10 2023-04-27 14 39 1 10 2023-04-27 15 33 1 10 2023-04-27 16 41 1 10 2023-04-27 17 61 1 10 2023-04-27 18 55 1 10 2023-04-27 19 0 1 10 2023-04-27 20 0 1 10 2023-04-27 21 0 1 10 2023-04-27 22 0 1 10 2023-04-27 23 0 1 11 2023-04-27 9 19 1 11 2023-04-27 10 31 1 11 2023-04-27 11 -999 1 11 2023-04-27 12 50 1 11 2023-04-27 null 61 1 11 2023-04-27 14 36 1 11 2023-04-27 15 34 1 11 2023-04-27 16 43 1 11 2023-04-27 17 55 1 11 2023-04-27 18 57 1 11 2023-04-27 19 0 1 11 2023-04-27 20 0 1 11 2023-04-27 21 0 1 11 2023-04-27 22 0 1 11 2023-04-27 23 0 1 12 2023-04-27 10 29 1 12 2023-04-27 11 38 1 12 2023-04-27 12 41 1 12 2023-04-27 13 61 1 12 2023-04-27 15 405 1 12 2023-04-27 16 37 1 12 2023-04-27 17 58 1 12 2023-04-27 18 61 1 12 2023-04-27 19 0 1 12 2023-04-27 20 0 1 12 2023-04-27 22 0 1 12 2023-04-27 23 0 2 1 2023-04-27 9 22 2 1 2023-04-27 10 40 2 1 2023-04-27 11 50 2 1 2023-04-27 12 47 2 1 2023-04-27 13 65 2 1 2023-04-27 14 44 2 1 2023-04-27 15 42 2 1 2023-04-27 16 41 2 1 2023-04-27 18 56 2 1 2023-04-27 19 0 2 1 2023-04-27 20 0 2 1 2023-04-27 21 0 2 1 2023-04-27 22 0 2 1 2023-04-27 23 0 2 2 2023-04-27 9 21 2 2 2023-04-27 10 34 2 2 2023-04-27 11 38 2 2 2023-04-27 1

In [0]:
clean_visiteurs = spark.sql("""
    SELECT 
        *
    FROM clean_visiteurs v
    WHERE v.store_id <= 10 AND v.sensor_id <= 12
    AND v.heure BETWEEN 9 AND 19
    AND v.date is not NULL
    AND v.nb_visiteurs BETWEEN 1 and 120 -- eleminer valeurs null et abiraintes
""")
clean_visiteurs.createOrReplaceTempView("clean_visiteurs")
display(clean_visiteurs)

store_id sensor_id date heure nb_visiteurs 1 1 2023-04-27 9 25 1 1 2023-04-27 10 55 1 1 2023-04-27 11 62 1 1 2023-04-27 12 64 1 1 2023-04-27 13 89 1 1 2023-04-27 14 52 1 1 2023-04-27 15 50 1 1 2023-04-27 16 48 1 1 2023-04-27 17 77 1 1 2023-04-27 18 89 1 2 2023-04-27 9 17 1 2 2023-04-27 11 35 1 2 2023-04-27 13 53 1 2 2023-04-27 14 33 1 2 2023-04-27 15 41 1 2 2023-04-27 16 41 1 2 2023-04-27 17 64 1 2 2023-04-27 18 64 1 3 2023-04-27 9 27 1 3 2023-04-27 10 47 1 3 2023-04-27 11 51 1 3 2023-04-27 12 59 1 3 2023-04-27 13 76 1 3 2023-04-27 14 47 1 3 2023-04-27 15 54 1 3 2023-04-27 16 51 1 3 2023-04-27 17 74 1 3 2023-04-27 18 79 1 4 2023-04-27 9 19 1 4 2023-04-27 10 30 1 4 2023-04-27 11 34 1 4 2023-04-27 12 41 1 4 2023-04-27 13 57 1 4 2023-04-27 14 42 1 4 2023-04-27 15 43 1 4 2023-04-27 16 41 1 4 2023-04-27 17 51 1 4 2023-04-27 18 65 1 5 2023-04-27 9 25 1 5 2023-04-27 11 54 1 5 2023-04-27 13 75 1 5 2023-04-27 14 51 1 5 2023-04-27 15 48 1 5 2023-04-27 16 51 1 5 2023-04-27 18 74 1 6 2023-04-27 9 20 1 6 2023-04-27 10 34 1 6 2023-04-27 11 38 1 6 2023-04-27 12 40 1 6 2023-04-27 13 60 1 6 2023-04-27 14 41 1 6 2023-04-27 16 36 1 6 2023-04-27 17 55 1 6 2023-04-27 18 49 1 7 2023-04-27 9 14 1 7 2023-04-27 10 21 1 7 2023-04-27 11 30 1 7 2023-04-27 12 32 1 7 2023-04-27 13 48 1 7 2023-04-27 14 31 1 7 2023-04-27 17 48 1 7 2023-04-27 18 47 1 8 2023-04-27 9 17 1 8 2023-04-27 10 23 1 8 2023-04-27 11 25 1 8 2023-04-27 13 49 1 8 2023-04-27 14 30 1 8 2023-04-27 15 29 1 8 2023-04-27 16 26 1 8 2023-04-27 17 39 1 8 2023-04-27 18 45 1 9 2023-04-27 9 30 1 9 2023-04-27 10 41 1 9 2023-04-27 11 53 1 9 2023-04-27 12 68 1 9 2023-04-27 13 77 1 9 2023-04-27 14 50 1 9 2023-04-27 15 53 1 9 2023-04-27 16 55 1 9 2023-04-27 17 87 1 9 2023-04-27 18 80 1 10 2023-04-27 9 16 1 10 2023-04-27 10 27 1 10 2023-04-27 12 43 1 10 2023-04-27 13 50 1 10 2023-04-27 14 39 1 10 2023-04-27 15 33 1 10 2023-04-27 16 41 1 10 2023-04-27 17 61 1 10 2023-04-27 18 55 1 11 2023-04-27 9 19 1 11 2023-04-27 10 31 1 11 2023-04-27 12 50 1 11 2023-04-27 14 36 1 11 2023-04-27 15 34 1 11 2023-04-27 16 43 1 11 2023-04-27 17 55 1 11 2023-04-27 18 57 1 12 2023-04-27 10 29 1 12 2023-04-27 11 38 1 12 2023-04-27 12 41 1 12 2023-04-27 13 61 1 12 2023-04-27 16 37 1 12 2023-04-27 17 58 1 12 2023-04-27 18 61 2 1 2023-04-27 9 22 2 1 2023-04-27 10 40 2 1 2023-04-27 11 50 2 1 2023-04-27 12 47 2 1 2023-04-27 13 65 2 1 2023-04-27 14 44 2 1 2023-04-27 15 42 2 1 2023-04-27 16 41 2 1 2023-04-27 18 56 2 2 2023-04-27 9 21 2 2 2023-04-27 10 34 2 2 2023-04-27 11 38 2 2 2023-04-27 12 52 2 2 2023-04-27 13 63 2 2 2023-04-27 14 40 2 2 2023-04-27 15 47 2 2 2023-04-27 16 47 2 2 2023-04-27 17 55 2 2 2023-04-27 18 64 2 3 2023-04-27 9 23 2 3 2023-04-27 10 30 2 3 2023-04-27 11 47 2 3 2023-04-27 13 78 2 3 2023-04-27 14 44 2 3 2023-04-27 15 48 2 3 2023-04-27 16 43 2 3 2023-04-27 18 63 2 4 2023-04-27 9 13 2 4 2023-04-27 11 24 2 4 2023-04-27 12 27 2 4 2023-04-27 13 35 2 4 2023-04-27 14 22 2 4 2023-04-27 15 23 2 4 2023-04-27 16 24 2 4 2023-04-27 17 38 2 4 2023-04-27 18 34 2 5 2023-04-27 9 12 2 5 2023-04-27 10 19 2 5 2023-04-27 11 22 2 5 2023-04-27 12 26 2 5 2023-04-27 13 40 2 5 2023-04-27 14 22 2 5 2023-04-27 15 25 2 5 2023-04-27 16 25 2 5 2023-04-27 17 32 2 5 2023-04-27 18 35 2 6 2023-04-27 9 19 2 6 2023-04-27 10 37 2 6 2023-04-27 11 42 2 6 2023-04-27 12 40 2 6 2023-04-27 13 63 2 6 2023-04-27 14 35 2 6 2023-04-27 15 41 2 6 2023-04-27 16 42 2 6 2023-04-27 17 64 2 6 2023-04-27 18 60 2 7 2023-04-27 9 20 2 7 2023-04-27 10 31 2 7 2023-04-27 11 44 2 7 2023-04-27 12 58 2 7 2023-04-27 13 73 2 7 2023-04-27 14 51 2 7 2023-04-27 15 41 2 7 2023-04-27 16 42 2 7 2023-04-27 17 68 2 8 2023-04-27 9 13 2 8 2023-04-27 10 21 2 8 2023-04-27 11 23 2 8 2023-04-27 12 27 2 8 2023-04-27 13 31 2 8 2023-04-27 14 21 2 8 2023-04-27 15 22 2 8 2023-04-27 16 26 2 8 2023-04-27 17 39 2 8 2023-04-27 18 36 2 9 2023-04-27 9 24 2 9 2023-04-27 13 60 2 9 2023-04-27 14 43 2 9 2023-04-27 15 39 2 9 2023-04-27 16 40 2 9 2023-04-27 17 69 2 9 2023-04-27 18 60 2 10 2023-04-27 9 21 2 10 

In [0]:
spark.sql("""
    -- table des dates attendues
    WITH dates_attendues AS (
        select d.date from
        (SELECT explode(sequence(DATE '2023-04-27', DATE '2025-04-27', 
        INTERVAL 1 DAY)
        ) AS date) as d
        where dayofweek(d.date) BETWEEN 2 AND 6
    ),
    -- ids des magasins et des capteurs
    identifiants_uniques AS (
        SELECT DISTINCT store_id, sensor_id
        FROM clean_visiteurs
    ),
    toutes_combinaisons AS (
        SELECT i.store_id, i.sensor_id, d.date
        FROM identifiants_uniques i
        CROSS JOIN dates_attendues d
    )

    select t.store_id, t.sensor_id, t.date
    from toutes_combinaisons t
    left join clean_visiteurs v
    on v.store_id = t.store_id
    and v.sensor_id = t.sensor_id
    and v.date = t.date
    where v.date is null
""").show()


+--------+---------+----+
|store_id|sensor_id|date|
+--------+---------+----+
+--------+---------+----+



On a tout les dates maintenat on va chercher les heures

Trouver les données manquantes

In [0]:
visiteurs_manquants = spark.sql("""
    -- table des dates attendues
    WITH heures_attendues AS (
        SELECT explode(sequence(9, 19)) AS heure
    ), 
    dates_attendues AS (
        select d.date from
        (SELECT explode(sequence(DATE '2023-04-27', DATE '2025-04-27', 
        INTERVAL 1 DAY)
        ) AS date) as d
        where dayofweek(d.date) BETWEEN 2 AND 6
    ),
    -- ids des magasins et des capteurs
    identifiants_uniques AS (
        SELECT DISTINCT store_id, sensor_id
        FROM clean_visiteurs
    ),
    toutes_combinaisons AS (
        SELECT i.store_id, i.sensor_id, d.date,h.heure
        FROM identifiants_uniques i
        CROSS JOIN dates_attendues d
        CROSS JOIN heures_attendues h
    )

    select t.store_id, t.sensor_id, t.date,t.heure
    from toutes_combinaisons t
    left join clean_visiteurs v
    on v.store_id = t.store_id
    and v.sensor_id = t.sensor_id
    and v.date = t.date
    and v.heure = t.heure
    where v.heure is null

""")
visiteurs_manquants.createOrReplaceTempView("visiteurs_manquants")
display(visiteurs_manquants)


store_id sensor_id date heure 5 5 2023-05-18 13 10 1 2023-06-12 19 1 7 2023-07-12 14 1 1 2023-05-22 14 8 6 2023-07-19 13 3 3 2023-06-05 19 1 8 2023-08-02 19 1 1 2023-05-24 12 7 4 2023-08-02 10 2 3 2023-05-29 19 2 5 2023-08-14 12 7 7 2023-07-14 16 2 1 2023-08-03 11 4 8 2023-06-08 19 8 5 2023-06-28 19 10 2 2023-06-16 19 9 5 2023-05-24 19 9 4 2023-05-24 15 4 4 2023-06-30 19 5 4 2023-06-07 15 4 7 2023-08-16 14 8 7 2023-07-21 10 7 1 2023-06-05 11 1 8 2023-09-01 9 1 10 2023-07-31 13 3 4 2023-08-16 14 2 3 2023-06-26 19 1 12 2023-08-16 11 7 4 2023-09-06 9 3 1 2023-08-08 18 4 4 2023-07-14 19 1 4 2023-06-23 9 2 8 2023-06-30 17 2 6 2023-07-28 19 8 5 2023-07-28 17 1 1 2023-07-06 12 4 9 2023-10-06 19 1 7 2023-09-06 19 9 1 2023-08-31 19 5 4 2023-07-07 17 4 8 2023-07-26 19 3 1 2023-09-01 19 7 1 2023-07-12 19 5 5 2023-07-27 19 6 2 2023-09-12 19 6 5 2023-10-18 12 6 1 2023-10-04 17 8 7 2023-08-31 19 7 3 2023-09-27 19 4 3 2023-10-11 19 9 6 2023-09-04 16 1 9 2023-10-23 19 10 2 2023-08-21 13 1 6 2023-10-24 19 8 7 2023-09-18 9 4 9 2023-11-10 19 8 4 2023-11-17 18 4 9 2023-11-14 15 4 9 2023-11-14 19 3 10 2023-08-09 19 4 6 2023-08-16 17 3 6 2023-10-18 19 10 4 2023-11-27 19 1 2 2023-09-19 19 2 1 2023-11-01 17 1 3 2023-10-12 12 4 3 2023-11-09 19 7 5 2023-11-22 19 1 10 2023-10-17 13 7 6 2023-09-15 15 5 7 2023-09-27 19 9 4 2023-08-21 19 2 5 2023-11-30 17 7 1 2023-08-28 19 5 6 2023-12-07 19 8 6 2023-11-14 16 7 7 2023-10-30 19 5 1 2023-09-13 19 2 6 2023-10-12 19 2 7 2023-11-28 19 6 6 2023-09-25 9 4 7 2023-11-16 9 8 7 2023-10-25 19 2 6 2023-10-19 18 7 2 2023-11-23 10 2 6 2023-10-19 9 2 9 2023-12-27 9 4 2 2023-09-18 19 1 8 2023-12-15 10 10 4 2024-01-05 9 7 6 2023-10-19 19 7 5 2024-01-03 17 9 1 2023-12-05 19 8 2 2023-10-02 11 7 8 2024-01-15 9 3 2 2023-12-11 19 10 1 2023-11-14 12 1 10 2023-11-30 19 4 6 2023-10-18 11 4 4 2023-11-07 12 8 6 2023-12-22 19 3 9 2024-01-03 19 5 6 2024-01-18 19 8 2 2023-10-09 19 1 7 2023-12-21 17 4 5 2024-01-02 9 4 5 2024-01-03 12 8 3 2023-12-06 16 1 1 2023-11-02 16 1 12 2023-12-20 19 8 4 2024-02-02 17 1 1 2023-11-06 19 2 4 2023-12-05 19 5 3 2023-12-08 19 4 5 2024-01-09 9 2 10 2024-02-06 15 7 2 2024-01-09 19 1 1 2023-11-10 17 1 9 2024-01-24 19 9 1 2023-12-28 12 4 9 2024-02-07 19 10 2 2023-11-29 19 4 6 2023-11-15 10 1 8 2024-02-05 18 6 6 2023-12-04 17 6 1 2024-02-02 16 8 6 2024-01-29 18 9 5 2023-11-13 14 1 9 2024-02-16 15 3 6 2024-02-05 13 3 3 2023-12-25 19 5 8 2024-01-08 11 10 1 2024-01-04 9 6 4 2024-03-05 14 10 1 2024-01-05 11 7 4 2024-02-22 9 2 3 2023-12-19 11 1 1 2023-12-26 9 8 5 2024-01-18 19 1 8 2024-03-08 14 7 1 2023-12-12 15 5 6 2024-03-22 16 10 5 2023-12-11 18 9 3 2024-01-18 14 3 10 2023-12-20 11 2 5 2024-03-22 16 3 9 2024-03-18 19 7 2 2024-03-08 17 1 6 2024-03-20 9 6 3 2024-04-01 12 2 6 2024-02-09 17 8 6 2024-03-14 9 3 4 2024-03-12 19 8 5 2024-02-12 12 3 6 2024-03-14 19 2 7 2024-04-03 12 6 5 2024-04-11 19 5 5 2024-01-24 15 8 1 2024-01-29 19 7 6 2024-02-02 13 1 2 2024-02-16 19 4 5 2024-04-01 19 3 3 2024-02-12 19 3 8 2024-01-19 15 1 7 2024-03-22 19 8 4 2024-04-30 19 2 10 2024-04-29 17 9 3 2024-02-21 19 3 9 2024-04-12 18 9 2 2024-02-15 15 5 8 2024-03-04 19 4 6 2024-02-01 18 3 4 2024-04-08 9 10 4 2024-05-14 17 7 6 2024-02-22 19 5 8 2024-03-19 19 2 7 2024-05-01 19 4 7 2024-04-19 19 2 8 2024-02-20 10 4 6 2024-02-19 9 9 7 2024-04-11 9 5 5 2024-03-01 9 7 6 2024-03-12 19 1 10 2024-04-11 19 6 2 2024-04-18 19 9 3 2024-03-25 17 6 2 2024-04-19 18 2 5 2024-05-24 19 1 9 2024-05-24 14 1 8 2024-05-28 18 4 2 2024-03-04 10 4 6 2024-03-14 15 9 2 2024-04-01 19 4 8 2024-03-27 18 5 2 2024-04-15 10 8 1 2024-03-27 10 8 4 2024-06-25 16 10 3 2024-04-08 19 5 6 2024-06-25 18 3 2 2024-05-23 19 2 10 2024-07-03 19 4 3 2024-06-12 13 3 10 2024-03-27 19 1 1 2024-04-09 19 4 3 2024-06-13 14 5 3 2024-05-13 9 6 1 2024-06-13 14 6 1 2024-06-14 12 5 7 2024-04-30 9 5 2 2024-05-06 9 1 12 2024-05-31 10 7 2 2024-06-14 17 1 10 2024-05-27 10 8 7 2024-05-27 19 9 2 2024-05-07 17 3 10 2024-04-15 19 9 7 2024-06-06 14 4 3 2024-07-04 10 4 1 2024-04-18 17 5 3 2024-06-05 19 5 6 202

In [0]:
visiteurs_manquants = spark.sql("""
    with moyenne_visiteurs as (
    select v.store_id, v.sensor_id, v.date, cast(avg(v.nb_visiteurs) AS int) as nb_visiteurs
    from clean_visiteurs v
    group by v.store_id, v.sensor_id, v.date
    )
    select v.*, mv.nb_visiteurs
    from visiteurs_manquants v
    inner join moyenne_visiteurs mv
    on v.store_id = mv.store_id
    and v.sensor_id = mv.sensor_id
    and v.date = mv.date

""")
visiteurs_manquants.createOrReplaceTempView("visiteurs_manquants")
display(visiteurs_manquants)

store_id sensor_id date heure nb_visiteurs 5 5 2023-05-18 13 36 10 1 2023-06-12 19 19 1 7 2023-07-12 14 39 1 1 2023-05-22 14 56 8 6 2023-07-19 13 50 3 3 2023-06-05 19 43 1 8 2023-08-02 19 39 1 1 2023-05-24 12 70 7 4 2023-08-02 10 61 2 3 2023-05-29 19 38 2 5 2023-08-14 12 19 7 7 2023-07-14 16 58 2 1 2023-08-03 11 46 4 8 2023-06-08 19 23 8 5 2023-06-28 19 34 10 2 2023-06-16 19 29 9 5 2023-05-24 19 49 9 4 2023-05-24 15 44 4 4 2023-06-30 19 38 5 4 2023-06-07 15 44 4 7 2023-08-16 14 52 8 7 2023-07-21 10 29 7 1 2023-06-05 11 20 1 8 2023-09-01 9 42 1 10 2023-07-31 13 32 3 4 2023-08-16 14 60 2 3 2023-06-26 19 37 1 12 2023-08-16 11 50 7 4 2023-09-06 9 59 3 1 2023-08-08 18 35 4 4 2023-07-14 19 37 1 4 2023-06-23 9 49 2 8 2023-06-30 17 28 2 6 2023-07-28 19 53 8 5 2023-07-28 17 33 1 1 2023-07-06 12 60 4 9 2023-10-06 19 55 1 7 2023-09-06 19 38 9 1 2023-08-31 19 39 5 4 2023-07-07 17 35 4 8 2023-07-26 19 29 3 1 2023-09-01 19 39 7 1 2023-07-12 19 32 5 5 2023-07-27 19 39 6 2 2023-09-12 19 25 6 5 2023-10-18 12 45 6 1 2023-10-04 17 29 8 7 2023-08-31 19 22 7 3 2023-09-27 19 54 4 3 2023-10-11 19 36 9 6 2023-09-04 16 31 1 9 2023-10-23 19 47 10 2 2023-08-21 13 17 1 6 2023-10-24 19 42 8 7 2023-09-18 9 19 4 9 2023-11-10 19 55 8 4 2023-11-17 18 32 4 9 2023-11-14 15 44 4 9 2023-11-14 19 44 3 10 2023-08-09 19 63 4 6 2023-08-16 17 50 3 6 2023-10-18 19 45 10 4 2023-11-27 19 20 1 2 2023-09-19 19 43 2 1 2023-11-01 17 53 1 3 2023-10-12 12 57 4 3 2023-11-09 19 30 7 5 2023-11-22 19 31 1 10 2023-10-17 13 42 7 6 2023-09-15 15 55 5 7 2023-09-27 19 34 9 4 2023-08-21 19 28 2 5 2023-11-30 17 24 7 1 2023-08-28 19 21 5 6 2023-12-07 19 28 8 6 2023-11-14 16 42 7 7 2023-10-30 19 39 5 1 2023-09-13 19 35 2 6 2023-10-12 19 45 2 7 2023-11-28 19 48 6 6 2023-09-25 9 22 4 7 2023-11-16 9 49 8 7 2023-10-25 19 28 2 6 2023-10-19 18 46 7 2 2023-11-23 10 28 2 6 2023-10-19 9 46 2 9 2023-12-27 9 62 4 2 2023-09-18 19 35 1 8 2023-12-15 10 41 10 4 2024-01-05 9 30 7 6 2023-10-19 19 45 7 5 2024-01-03 17 30 9 1 2023-12-05 19 40 8 2 2023-10-02 11 22 7 8 2024-01-15 9 29 3 2 2023-12-11 19 22 10 1 2023-11-14 12 24 1 10 2023-11-30 19 41 4 6 2023-10-18 11 52 4 4 2023-11-07 12 29 8 6 2023-12-22 19 55 3 9 2024-01-03 19 34 5 6 2024-01-18 19 29 8 2 2023-10-09 19 24 1 7 2023-12-21 17 28 4 5 2024-01-02 9 45 4 5 2024-01-03 12 48 8 3 2023-12-06 16 36 1 1 2023-11-02 16 69 1 12 2023-12-20 19 48 8 4 2024-02-02 17 34 1 1 2023-11-06 19 51 2 4 2023-12-05 19 25 5 3 2023-12-08 19 48 4 5 2024-01-09 9 43 2 10 2024-02-06 15 44 7 2 2024-01-09 19 26 1 1 2023-11-10 17 73 1 9 2024-01-24 19 69 9 1 2023-12-28 12 40 4 9 2024-02-07 19 53 10 2 2023-11-29 19 28 4 6 2023-11-15 10 55 1 8 2024-02-05 18 26 6 6 2023-12-04 17 20 6 1 2024-02-02 16 31 8 6 2024-01-29 18 30 9 5 2023-11-13 14 32 1 9 2024-02-16 15 67 3 6 2024-02-05 13 26 3 3 2023-12-25 19 39 5 8 2024-01-08 11 24 10 1 2024-01-04 9 28 6 4 2024-03-05 14 38 10 1 2024-01-05 11 33 7 4 2024-02-22 9 58 2 3 2023-12-19 11 49 1 1 2023-12-26 9 62 8 5 2024-01-18 19 28 1 8 2024-03-08 14 40 7 1 2023-12-12 15 26 5 6 2024-03-22 16 35 10 5 2023-12-11 18 28 9 3 2024-01-18 14 26 3 10 2023-12-20 11 61 2 5 2024-03-22 16 32 3 9 2024-03-18 19 22 7 2 2024-03-08 17 32 1 6 2024-03-20 9 51 6 3 2024-04-01 12 31 2 6 2024-02-09 17 50 8 6 2024-03-14 9 40 3 4 2024-03-12 19 52 8 5 2024-02-12 12 23 3 6 2024-03-14 19 38 2 7 2024-04-03 12 57 6 5 2024-04-11 19 38 5 5 2024-01-24 15 46 8 1 2024-01-29 19 33 7 6 2024-02-02 13 56 1 2 2024-02-16 19 53 4 5 2024-04-01 19 34 3 3 2024-02-12 19 38 3 8 2024-01-19 15 61 1 7 2024-03-22 19 38 8 4 2024-04-30 19 30 2 10 2024-04-29 17 33 9 3 2024-02-21 19 32 3 9 2024-04-12 18 33 9 2 2024-02-15 15 32 5 8 2024-03-04 19 21 4 6 2024-02-01 18 43 3 4 2024-04-08 9 43 10 4 2024-05-14 17 24 7 6 2024-02-22 19 40 5 8 2024-03-19 19 27 2 7 2024-05-01 19 52 4 7 2024-04-19 19 52 2 8 2024-02-20 10 25 4 6 2024-02-19 9 36 9 7 2024-04-11 9 37 5 5 2024-03-01 9 49 7 6 2024-03-12 19 45 1 10 2024-04-11 19 41 6 2 2024-04-18 19 25 9 3 2024-03-25 17 19 6 2 2024-04-19 18 30 2 5 2024-05-24 19 29 1 9 2024-

In [0]:
clean_visiteurs = spark.sql("""
    SELECT store_id, sensor_id, date, heure, nb_visiteurs
    FROM clean_visiteurs

    UNION ALL

    SELECT store_id, sensor_id, date, heure, nb_visiteurs
    FROM visiteurs_manquants
""")
display(clean_visiteurs)


store_id sensor_id date heure nb_visiteurs 1 1 2023-04-27 9 25 1 1 2023-04-27 10 55 1 1 2023-04-27 11 62 1 1 2023-04-27 12 64 1 1 2023-04-27 13 89 1 1 2023-04-27 14 52 1 1 2023-04-27 15 50 1 1 2023-04-27 16 48 1 1 2023-04-27 17 77 1 1 2023-04-27 18 89 1 2 2023-04-27 9 17 1 2 2023-04-27 11 35 1 2 2023-04-27 13 53 1 2 2023-04-27 14 33 1 2 2023-04-27 15 41 1 2 2023-04-27 16 41 1 2 2023-04-27 17 64 1 2 2023-04-27 18 64 1 3 2023-04-27 9 27 1 3 2023-04-27 10 47 1 3 2023-04-27 11 51 1 3 2023-04-27 12 59 1 3 2023-04-27 13 76 1 3 2023-04-27 14 47 1 3 2023-04-27 15 54 1 3 2023-04-27 16 51 1 3 2023-04-27 17 74 1 3 2023-04-27 18 79 1 4 2023-04-27 9 19 1 4 2023-04-27 10 30 1 4 2023-04-27 11 34 1 4 2023-04-27 12 41 1 4 2023-04-27 13 57 1 4 2023-04-27 14 42 1 4 2023-04-27 15 43 1 4 2023-04-27 16 41 1 4 2023-04-27 17 51 1 4 2023-04-27 18 65 1 5 2023-04-27 9 25 1 5 2023-04-27 11 54 1 5 2023-04-27 13 75 1 5 2023-04-27 14 51 1 5 2023-04-27 15 48 1 5 2023-04-27 16 51 1 5 2023-04-27 18 74 1 6 2023-04-27 9 20 1 6 2023-04-27 10 34 1 6 2023-04-27 11 38 1 6 2023-04-27 12 40 1 6 2023-04-27 13 60 1 6 2023-04-27 14 41 1 6 2023-04-27 16 36 1 6 2023-04-27 17 55 1 6 2023-04-27 18 49 1 7 2023-04-27 9 14 1 7 2023-04-27 10 21 1 7 2023-04-27 11 30 1 7 2023-04-27 12 32 1 7 2023-04-27 13 48 1 7 2023-04-27 14 31 1 7 2023-04-27 17 48 1 7 2023-04-27 18 47 1 8 2023-04-27 9 17 1 8 2023-04-27 10 23 1 8 2023-04-27 11 25 1 8 2023-04-27 13 49 1 8 2023-04-27 14 30 1 8 2023-04-27 15 29 1 8 2023-04-27 16 26 1 8 2023-04-27 17 39 1 8 2023-04-27 18 45 1 9 2023-04-27 9 30 1 9 2023-04-27 10 41 1 9 2023-04-27 11 53 1 9 2023-04-27 12 68 1 9 2023-04-27 13 77 1 9 2023-04-27 14 50 1 9 2023-04-27 15 53 1 9 2023-04-27 16 55 1 9 2023-04-27 17 87 1 9 2023-04-27 18 80 1 10 2023-04-27 9 16 1 10 2023-04-27 10 27 1 10 2023-04-27 12 43 1 10 2023-04-27 13 50 1 10 2023-04-27 14 39 1 10 2023-04-27 15 33 1 10 2023-04-27 16 41 1 10 2023-04-27 17 61 1 10 2023-04-27 18 55 1 11 2023-04-27 9 19 1 11 2023-04-27 10 31 1 11 2023-04-27 12 50 1 11 2023-04-27 14 36 1 11 2023-04-27 15 34 1 11 2023-04-27 16 43 1 11 2023-04-27 17 55 1 11 2023-04-27 18 57 1 12 2023-04-27 10 29 1 12 2023-04-27 11 38 1 12 2023-04-27 12 41 1 12 2023-04-27 13 61 1 12 2023-04-27 16 37 1 12 2023-04-27 17 58 1 12 2023-04-27 18 61 2 1 2023-04-27 9 22 2 1 2023-04-27 10 40 2 1 2023-04-27 11 50 2 1 2023-04-27 12 47 2 1 2023-04-27 13 65 2 1 2023-04-27 14 44 2 1 2023-04-27 15 42 2 1 2023-04-27 16 41 2 1 2023-04-27 18 56 2 2 2023-04-27 9 21 2 2 2023-04-27 10 34 2 2 2023-04-27 11 38 2 2 2023-04-27 12 52 2 2 2023-04-27 13 63 2 2 2023-04-27 14 40 2 2 2023-04-27 15 47 2 2 2023-04-27 16 47 2 2 2023-04-27 17 55 2 2 2023-04-27 18 64 2 3 2023-04-27 9 23 2 3 2023-04-27 10 30 2 3 2023-04-27 11 47 2 3 2023-04-27 13 78 2 3 2023-04-27 14 44 2 3 2023-04-27 15 48 2 3 2023-04-27 16 43 2 3 2023-04-27 18 63 2 4 2023-04-27 9 13 2 4 2023-04-27 11 24 2 4 2023-04-27 12 27 2 4 2023-04-27 13 35 2 4 2023-04-27 14 22 2 4 2023-04-27 15 23 2 4 2023-04-27 16 24 2 4 2023-04-27 17 38 2 4 2023-04-27 18 34 2 5 2023-04-27 9 12 2 5 2023-04-27 10 19 2 5 2023-04-27 11 22 2 5 2023-04-27 12 26 2 5 2023-04-27 13 40 2 5 2023-04-27 14 22 2 5 2023-04-27 15 25 2 5 2023-04-27 16 25 2 5 2023-04-27 17 32 2 5 2023-04-27 18 35 2 6 2023-04-27 9 19 2 6 2023-04-27 10 37 2 6 2023-04-27 11 42 2 6 2023-04-27 12 40 2 6 2023-04-27 13 63 2 6 2023-04-27 14 35 2 6 2023-04-27 15 41 2 6 2023-04-27 16 42 2 6 2023-04-27 17 64 2 6 2023-04-27 18 60 2 7 2023-04-27 9 20 2 7 2023-04-27 10 31 2 7 2023-04-27 11 44 2 7 2023-04-27 12 58 2 7 2023-04-27 13 73 2 7 2023-04-27 14 51 2 7 2023-04-27 15 41 2 7 2023-04-27 16 42 2 7 2023-04-27 17 68 2 8 2023-04-27 9 13 2 8 2023-04-27 10 21 2 8 2023-04-27 11 23 2 8 2023-04-27 12 27 2 8 2023-04-27 13 31 2 8 2023-04-27 14 21 2 8 2023-04-27 15 22 2 8 2023-04-27 16 26 2 8 2023-04-27 17 39 2 8 2023-04-27 18 36 2 9 2023-04-27 9 24 2 9 2023-04-27 13 60 2 9 2023-04-27 14 43 2 9 2023-04-27 15 39 2 9 2023-04-27 16 40 2 9 2023-04-27 17 69 2 9 2023-04-27 18 60 2 10 2023-04-27 9 21 2 10 

PySpark

In [0]:
clean_visiteurs = clean_visiteurs \
    .withColumn("store_id", F.col("store_id").cast("int")) \
    .withColumn("sensor_id", F.col("sensor_id").cast("int"))


Check des doublons

In [0]:
clean_visiteurs.groupBy("date", "heure", "store_id", "sensor_id") \
    .agg(F.count("*").alias("nb")) \
    .filter(F.col("nb") > 1) \
    .show()

+----+-----+--------+---------+---+
|date|heure|store_id|sensor_id| nb|
+----+-----+--------+---------+---+
+----+-----+--------+---------+---+



In [0]:
clean_visiteurs.count()

476586

In [0]:
clean_visiteurs = clean_visiteurs.dropDuplicates(
    ["date", "heure", "store_id", "sensor_id"]
)

In [0]:
clean_visiteurs.count()

476586

In [0]:
clean_visiteurs.select(F.min(F.col("date")), F.max(F.col("date"))).show()

+----------+----------+
| min(date)| max(date)|
+----------+----------+
|2023-04-27|2025-04-25|
+----------+----------+



In [0]:
clean_visiteurs.select("nb_visiteurs").describe().show()

+-------+------------------+
|summary|      nb_visiteurs|
+-------+------------------+
|  count|            476586|
|   mean|39.407804677434925|
| stddev| 16.34371888696327|
|    min|                 1|
|    max|               120|
+-------+------------------+



In [0]:
display(clean_visiteurs)

store_id sensor_id date heure nb_visiteurs 5 2 2023-04-27 10 20 7 4 2023-04-27 17 62 8 6 2023-04-27 16 36 3 3 2023-04-28 13 82 3 7 2023-04-28 15 62 4 7 2023-04-28 12 59 8 6 2023-04-28 13 69 2 8 2023-05-01 16 19 7 3 2023-05-01 11 38 2 8 2023-05-02 11 22 4 4 2023-05-03 13 53 6 3 2023-05-03 12 47 2 6 2023-05-04 11 38 7 4 2023-05-04 13 60 3 1 2023-05-05 11 41 3 10 2023-05-05 14 49 9 7 2023-05-05 12 59 3 8 2023-05-08 10 31 3 10 2023-05-08 13 50 5 4 2023-05-08 17 47 7 1 2023-05-08 12 20 9 1 2023-05-08 10 24 2 6 2023-05-09 18 53 6 1 2023-05-09 18 36 6 3 2023-05-09 15 35 7 7 2023-05-09 12 58 8 5 2023-05-09 13 45 8 6 2023-05-09 14 40 4 9 2023-05-10 14 52 7 3 2023-05-10 10 44 2 3 2023-05-11 11 45 3 4 2023-05-11 17 79 1 6 2023-05-12 10 45 3 9 2023-05-12 12 39 4 3 2023-05-12 15 30 4 4 2023-05-12 11 30 9 5 2023-05-12 17 1 5 5 2023-05-15 10 22 7 1 2023-05-15 11 22 3 4 2023-05-16 13 61 5 4 2023-05-16 15 30 7 6 2023-05-16 16 44 8 6 2023-05-16 15 41 8 7 2023-05-16 9 11 10 5 2023-05-16 9 16 1 10 2023-05-17 12 60 2 2 2023-05-17 10 34 2 7 2023-05-17 15 50 3 3 2023-05-17 16 61 7 4 2023-05-17 14 46 5 8 2023-05-18 14 25 2 5 2023-05-19 18 38 2 6 2023-05-19 17 73 3 3 2023-05-19 12 72 4 4 2023-05-19 14 35 5 1 2023-05-22 13 34 7 5 2023-05-22 15 21 8 5 2023-05-22 14 19 10 5 2023-05-22 16 25 1 2 2023-05-23 15 36 4 1 2023-05-23 14 23 9 4 2023-05-23 11 30 1 7 2023-05-24 9 19 1 11 2023-05-24 13 75 2 2 2023-05-24 18 63 6 1 2023-05-24 13 45 6 2 2023-05-24 17 47 7 4 2023-05-24 14 56 9 2 2023-05-24 18 62 2 7 2023-05-25 15 51 3 9 2023-05-25 12 33 4 9 2023-05-25 14 35 5 8 2023-05-25 13 42 1 1 2023-05-26 11 71 5 3 2023-05-26 9 19 6 4 2023-05-26 17 69 10 3 2023-05-26 13 64 1 5 2023-05-29 12 54 4 1 2023-05-29 12 22 10 2 2023-05-29 13 31 1 6 2023-05-30 10 36 2 6 2023-05-30 13 69 3 10 2023-05-30 15 48 4 7 2023-05-30 10 37 8 3 2023-05-30 13 43 3 8 2023-05-31 10 47 3 9 2023-05-31 10 25 5 3 2023-05-31 14 45 7 2 2023-05-31 12 33 8 6 2023-05-31 16 48 1 12 2023-06-01 14 39 1 9 2023-06-02 9 33 2 1 2023-06-02 13 69 1 2 2023-06-05 18 48 2 3 2023-06-05 13 61 3 3 2023-06-05 18 51 9 6 2023-06-05 10 24 10 3 2023-06-05 14 23 2 1 2023-06-06 16 44 7 4 2023-06-06 12 51 9 2 2023-06-06 11 41 3 7 2023-06-07 16 52 5 2 2023-06-07 18 51 6 5 2023-06-07 18 53 8 1 2023-06-07 11 47 8 5 2023-06-07 18 52 10 3 2023-06-07 14 45 2 10 2023-06-08 15 46 4 2 2023-06-08 10 31 5 1 2023-06-08 16 25 5 8 2023-06-08 10 20 10 1 2023-06-08 18 37 6 5 2023-06-09 13 66 8 1 2023-06-09 14 46 10 4 2023-06-09 13 37 2 1 2023-06-12 13 56 2 10 2023-06-12 9 15 3 2 2023-06-12 13 32 7 3 2023-06-12 18 50 2 3 2023-06-13 17 73 3 5 2023-06-13 16 40 3 10 2023-06-13 14 45 5 6 2023-06-13 9 13 1 1 2023-06-14 10 60 3 9 2023-06-14 16 32 8 3 2023-06-14 12 40 10 4 2023-06-14 10 22 2 2 2023-06-15 18 61 2 3 2023-06-15 9 25 2 7 2023-06-15 11 52 5 6 2023-06-15 9 14 7 1 2023-06-15 10 20 8 1 2023-06-15 17 56 9 3 2023-06-15 18 42 10 1 2023-06-15 17 29 10 5 2023-06-15 18 52 3 1 2023-06-16 10 27 6 5 2023-06-16 13 65 3 8 2023-06-19 11 42 4 1 2023-06-19 9 8 8 4 2023-06-20 15 28 9 5 2023-06-20 12 46 8 6 2023-06-21 14 55 8 7 2023-06-21 11 25 2 2 2023-06-22 17 70 2 8 2023-06-22 16 27 5 5 2023-06-22 10 29 8 1 2023-06-22 18 56 8 6 2023-06-22 15 39 1 4 2023-06-23 18 76 3 8 2023-06-23 11 51 4 9 2023-06-23 12 57 5 7 2023-06-23 10 29 9 4 2023-06-23 10 35 9 5 2023-06-23 13 65 3 9 2023-06-26 9 10 10 2 2023-06-26 18 23 3 7 2023-06-27 15 50 10 1 2023-06-27 16 23 6 3 2023-06-28 15 37 4 5 2023-06-30 15 46 4 8 2023-06-30 14 24 9 1 2023-06-30 18 62 3 6 2023-07-03 14 25 1 10 2023-07-04 14 33 4 5 2023-07-04 14 42 1 4 2023-07-05 10 40 2 10 2023-07-05 11 51 3 10 2023-07-05 18 85 10 3 2023-07-05 18 62 4 4 2023-07-06 10 24 7 2 2023-07-06 16 26 1 6 2023-07-07 12 1 3 3 2023-07-07 12 58 7 4 2023-07-07 9 24 9 3 2023-07-07 11 29 1 5 2023-07-10 17 56 3 6 2023-07-10 11 27 8 6 2023-07-10 18 50 9 6 2023-07-10 13 40 3 5 2023-07-11 13 67 3 9 2023-07-11 13 36 5 7 2023-07-11 15 29 10 4 2023-07-11 16 21 1 1 2023-07-13 16 47 1 10 2023-07-13 15 38 1 12 2023-07-13 16 40 1 12 2023-07-13 

In [0]:
try:
    clean_visiteurs.write.jdbc(
        url=jdbcUrl,
        table="analytics.visiteurs",
        mode="append",  # ou "overwrite" selon usage
        properties=connectionProperties
    )
    print("Données insérées avec succès dans analytics.visiteurs.")
except Exception as e:
    print("Erreur lors de l'insertion dans la base SQL :")
    print(str(e))

Données insérées avec succès dans analytics.visiteurs.
